# **AP155 Lab Assignment**
## Module 5: Partial Differential Equations

_Instructions_: Answer each problem as completely as you can. Discuss **all** your answers as clearly and concisely as possible.

_Scoring Criteria_: 50% - *correctness of code*; 50% - *discussion of the code and results*. Maximum score is **100 points**.



### Student Information

_Full Name (Last Name, First Name)_: Red Christian F. Hernandez\
_Student No._: 2022-03646\
_Section_: THV-TX-2

### Submission Information

_Date and Time Submitted (most recent upload)_: 10:10 PM / November 16,2024

**HONOR PLEDGE** I affirm that I have upheld the highest principles of honesty and integrity in my academic work and that this lab assignment is my own work.

**Sign here with your full name: Red Christian F. Hernandez**

### Grading Information (c/o Lab Instructor)

TOTAL SCORE: **[]**/100

Score breakdown:
* Problem 1 - []/100

_Date and Time Scored (MM/DD/YYYY HH:MM AM/PM):_

### PROBLEM 1
**The Schrodinger equation and the Crank-Nicolson method**

_Refer to Exercise 9.8 in the Newman text._ In this problem, you will use the Crank-Nicolson method to solve the full time-dependent Schrodinger equation and hence develop a picture of how a wavefunction evolves over time.

Consider an electron (mass $M = 9.109 \times 10^{-31}$ kg) in a box of length $L = 10^{-8}$ m. Suppose that at time $t = 0$ the wavefunction of the electron has the form

$$ \psi(x,0) = \exp\left[-\frac{(x-x_0)^2}{2\sigma^2}\right]e^{i\kappa x},$$
where $x_0 = \frac{L}{2}$, $\sigma = 1 \times 10^{-10}$ m, $\kappa = 5 \times 10^{10} {\rm m}^{-1}$,  and $\psi = 0$ on the walls at $x = 0$ and $x = L$.

1. Perform a single step of the Crank-Nicolson method for this electron, calculating the vector $\psi(t)$ of values of the wavefunction, given the initial wavefunction above and using $N = 1000$ spatial slices with $a = L/N$. Your program will have to perform the following steps. First, given the vector $\psi(0)$ at $t = 0$, you will have to multiply by the matrix $\bf{B}$ to get a vector $\bf{v} = \bf{B}\psi$. Because of the tridiagonal form of $\bf{B}$, this is fairly simple. The $i$th component of $\bf{v}$ is given by
$$ v_i = b_1\psi_i + b_2(\psi_{i+1} + \psi_{i-1}).$$

   You will also have to choose a value for the time-step $h$. A reasonable choice is $h = 10^{-18}$ s. *(30 pts.)*

2. Second you will have to solve the linear system ${\bf Ax}= {\bf v}$ for $\bf{x}$, which gives you the new value of $\psi$. You could do this using a standard linear equation solver like the function $\tt solve$ in numpy's $\tt linalg$. *(20 pts.)*

3. Once you have the code in place to perform a single step of the calculation, extend your program to perform repeated steps and hence solve for $\psi$ at a sequence of times a separation $h$ apart. Note that the matrix $\bf A$ is independent of time, so it doesn't change from one step to another. You can set up the matrix just once and then keep on reusing it for every step. *(30 pts.)*

4. Make an animation of the solution by displaying the real part of the wavefunction at each time-step. You can use the function rate from the package visual to ensure a smooth frame-rate for your animation-- see Section 3.5 on page 117 of the Newman text.

   Run your animation for a while and describe what you see. Write a few sentences explaining in physics terms what is going on in the system. *(20 pts.)*

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython import display # we import IPython in order to have the ability to create a display object with given data

# we initilize the needed constants
L = 1e-8       # length of the box (meters)
m = 9.109e-31  # mass of electron (kilograms)
ℏ = 1.0545718e-34  # planck's constant / 2π
N = 1000       # number of spatial slices
dx = L / N     # spacial step size
h = 1e-18      # time-step

x = np.linspace(0, L, N) # discretized spacial grid points between 0 and L

x0 = L / 2 # we set the initial position of the wave packet to be at the center of the box (L/2)
σ = 1e-10 # spread of gaussian wave packet
κ = 5e10 # wave number corresponding to particle's momentum

# psi_initial represents the initial wave function of the particle
# it has two components which are exp(-(x-x0)**2/(2*σ**2)) and np.exp(1j*κ*x)
# exp(-(x-x0)**2/(2*σ**2)) represents the gaussian-shaped probability distribution
# np.exp(1j*κ*x) represents the plane wave that oscillates in space
psi_initial = np.exp(-(x-x0)**2/(2*σ**2)) * np.exp(1j*κ*x)

# matrix coefficients derived from the discretized schrodinger equation using crank-nicholson
a1 = 1+1j*ℏ*h/(2*m*dx**2)
a2 = -1j*ℏ*h/(2*m*dx**2)/2
b1 = 1-1j*ℏ*h/(2*m*dx**2)
b2 = 1j*ℏ*h/(2*m*dx**2)/2

# we initialize a matrix of N x N size (1000x1000) filled with zeros as its element with complex as element type
A = np.zeros((N, N), dtype=complex)
for i in range(N): # we iterate over N elements
    A[i, i] = a1  # we set A[i, i] which is the main diagonal with its values as a1
    if i > 0: # if we go over the first row
        A[i, i-1] = a2  # we set the value just below the diagonal as a2
    if i < N - 1: # if we are not yet over the last row
        A[i, i+1] = a2  # we set the value just above the main diagonal as a2

# we initialize a matrix of N x N size (1000x1000) filled with zeros as its element with complex as element type
B = np.zeros((N, N), dtype=complex)
for i in range(N): # we iterate over N elements
    B[i, i] = b1  # we set B[i, i] which is the main diagonal with its values as b1
    if i > 0: # if we go over the first row
        B[i, i-1] = b2  # we set the value just below the diagonal as b2
    if i < N - 1: # if we are not yet over the last row
        B[i, i+1] = b2  # we set the value just above the main diagonal as a2

psi = psi_initial.copy() # we preserve the initial wavefunction by copying it as an array called psi
                         # psi describes the evolving state of the wavefunction whilst separte from the psi_initial keeping it intact all throughout the simulation

# we define a function that will simulate/solve the wavefunctions evolution by solving linear systems
def evolve(psi):
    b = B @ psi # we multiply matrix B with the current wave function
    psi_next = np.linalg.solve(A, b) # we solve for the next wavefunction
    return psi_next # we get the result for the next wavefunction

# set up plot for animation
fig, ax = plt.subplots() # we define a figure and axes
line, = ax.plot(x, psi.real, color="blue", lw=1) # we create a line plot on the ax axes and we extract the real component of the wave function
ax.set_xlim(0, L) # we set the limits for the x axis from 0 to L
ax.set_ylim(-1, 1) # we set the limits from the y axis from -1 to 1
ax.set_xlabel("x") # x axis label
ax.set_ylabel("Re(ψ)") # y axis label
ax.set_title("Real Part of the Wavefunction (Animation)") # title

# animation function
def update(frame):
    global psi # we represent the psi variable as global variable to ensure that, it actually evolves and represents the wavefunction as time progresses
    psi = evolve(psi) # the wave function psi will be applied function evolve() and will update based on its previous state
    line.set_ydata(psi.real)  # we update the y values with the new found values for the real part of the wave function psi
    return line, # this returns the updated plot at each frame

# creating and running animation
# we first define ani as a function animation with elements
# fig -> which defines a figure with axes
# update -> we call upon the update function for every frame of the animation to update the plot
# frames -> we set this simulation to run for 4000 frames
# interval -> defined as the elapsed time for each frame in milliseconds
ani = FuncAnimation(fig, update, frames = 4000, interval=10)
video = ani.to_html5_video() # we convert the animation into an html video format
html = display.HTML(video) # we create an html object
display.display(html) # we display the html object into the jupyter notebook
plt.close() # we close the figure plot window since the html video is already being displayed

The simulation begins at the middle of the potential well with a gaussian shape modulated by plane wave factor introducing oscillations in the given wave. the initial wave is smooth and localized and moves in the x direction due to wave number.

After the wave hits the boundaries of infinite potential, it gets reflected back in the opposite direction (given that it can't exist outside the box) forming standing wave patterns exhibiting interference patterns.

The standing wave is a result of superposition of the moving wave and its counter part exhibiting constructive interference and destructive interference.

